# [Maximum Path Sum I](https://projecteuler.net/problem=18)

As the problem notes, we could brute force every single path through this triangle, since there aren't that many, relatively speaking. But we're going to get a tougher version in [problem 67](https://projecteuler.net/problem=67), so if we make the effort now, we can kill two birds with one stone.

First, let's encode the triangle as a list of lists:

In [1]:
    triangle = [[75],
                [95, 64],
                [17, 47, 82],
                [18, 35, 87, 10],
                [20, 4, 82, 47, 65],
                [19, 1, 23, 75, 3, 34],
                [88, 2, 77, 73, 7, 63, 67],
                [99, 65, 4, 28, 6, 16, 70, 92],
                [41, 41, 26, 56, 83, 40, 80, 70, 33],
                [41, 48, 72, 33, 47, 32, 37, 16, 94, 29],
                [53, 71, 44, 65, 25, 43, 91, 52, 97, 51, 14],
                [70, 11, 33, 28, 77, 73, 17, 78, 39, 68, 17, 57],
                [91, 71, 52, 38, 17, 14, 91, 43, 58, 50, 27, 29, 48],
                [63, 66, 4, 68, 89, 53, 67, 30, 73, 16, 69, 87, 40, 31],
                [4, 62, 98, 27, 23, 9, 70, 98, 73, 93, 38, 53, 60, 4, 23]]

There are a couple of important things to note about this problem. First, looking at the triangle, try to see how there are two "sub-triangles" below the top value, 75 (it's easier to see this on the original page rather than in the list-of-lists). One sub-triangle has a top value of 95, then the next row is 17 and 47, and the next row is 18, 35, and 87, and so on.
```
       95
     17  47
   18  35  87
 ⋰     ⋮     ⋱
```

The other sub-triangle has a top value of 64, and the next row is 47 and 82, and so on.
```
       64
     47  82
   35  87  10
 ⋰     ⋮     ⋱
```

If we think a little abstractly, the maximum path sum (MPS) through *the whole triangle* must equal the sum of the topmost value (75) with the larger of the MPSs through *each sub-triangle*. This fact holds for the lower layers as well: the MPS for the sub-triangle with top value 95 depends on the MPSs for the sub-triangles with top values 17 and 47, and the MPS for the sub-triangle with top value 64 depends on the MPSs for the sub-triangles with top values 47 and 82, and so on and so on.

Because of this, the problem is said to have [optimal substructure](https://en.wikipedia.org/wiki/Optimal_substructure). In short, we find the MPS through the whole triangle by solving smaller and smaller subproblems, i.e. MPSs through sub-triangles. Eventually we will reach a base case: one of the values in the bottom-most layer of the triangle, where the maximum path sum of that "sub-triangle" is just the value itself.

There's another important thing to consider: in trying to find the MPS through the 95-sub-triangle, we have to find the MPS through the 47-sub-triangle. Similarly, in trying to find the MPS through the 64-sub-triangle, we *also* have to find the MPS through the 47-sub-triangle. This reoccurrence of subproblems happens more and more frequently in the lower layers, as well. In other words, there are [overlapping subproblems](https://en.wikipedia.org/wiki/Overlapping_subproblems).

When a problem has optimal substructure and overlapping subproblems, we can use [dynamic programming](https://en.wikipedia.org/wiki/Dynamic_programming). We can employ either a top-down or bottom-up approach.

## Top-down Method
This approach recusively finds the maximum path sums of each sub-triangle starting from the topmost value, similarly to what's described above. The `cache` decorator is used to memoize and avoid recomputing MPSs for any overlapping sub-triangles. This is crucial to the speed of a top-down approach; without memoization, we will recompute the solutions to overlapping subproblems way too often.

In [2]:
from functools import cache

@cache
def max_path_sum(tri):
    if tri == tuple():
        return 0

    left = tuple(row[:-1] for row in tri[1:])
    right = tuple(row[1:] for row in tri[1:])
    return tri[0][0] + max(max_path_sum(left), max_path_sum(right))

One slight wrinkle to this approach is that to use the `cache` decorator, the inputs to our function need to be [hashable](https://docs.python.org/3/glossary.html#term-hashable). Lists are not hashable, but tuples are, so we can convert our triangle to a tuple of tuples.

In [3]:
max_path_sum(tuple(tuple(row) for row in triangle))

1074

## Bottom-up Method
Another approach is to instead find the MPSs of the very smallest sub-triangles first, then use those MPSs to find the MPSs in the next layer up. This doesn't require memoization, since by starting with the smallest subproblems, we ensure they are only computed once.

In [4]:
def max_path_sum(tri):
    for i in reversed(range(0, len(tri) - 1)):
        for j in range(0, len(tri[i])):
            tri[i][j] += max(tri[i+1][j], tri[i+1][j+1])
            
    return tri[0][0]

max_path_sum(triangle)

1074